In [1]:
import pandas as pd
import numpy as np
from textblob import TextBlob, Word
import matplotlib.pyplot as plt
import seaborn as sns
sns.set(color_codes=True)
from sklearn.model_selection import train_test_split
import nltk
from nltk.corpus import stopwords, sentiwordnet as swn
from nltk.stem import WordNetLemmatizer
from nltk import ngrams
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation
import collections
!pip install vaderSentiment
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
#from stop_words_list import stop_words_list
#from wn_affect import wn_affect 
import matplotlib.pyplot as plt
from wordcloud import WordCloud

In [2]:
pip install WordCloud

In [3]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [4]:
import os
os.getcwd()

'/content'

In [5]:
data = pd.read_csv("seat.csv")

In [6]:
data.head()

airline_name  ... recommended
0            aegean-airlines  ...           1
1            aegean-airlines  ...           1
2                 aer-lingus  ...           1
3                 aer-lingus  ...           0
4  aeroflot-russian-airlines  ...           1

[5 rows x 21 columns]

In [7]:
data.isna().sum()

airline_name              0
link                      0
title                     0
author                    0
author_country            8
date                      0
content                   0
aircraft                  0
seat_layout               6
date_flown             1145
cabin_flown               6
type_traveller         1140
overall_rating            1
seat_legroom_rating       0
seat_recline_rating       0
seat_width_rating         0
aisle_space_rating        0
viewing_tv_rating        29
power_supply_rating    1196
seat_storage_rating    1145
recommended               0
dtype: int64

In [8]:
train, test = train_test_split(data, test_size=0.2)

In [9]:
len(train.index)

1006

In [10]:
len(test.index)

252

# DataPreprocessing

First step is tokenization which converts the text into sentences and the sentences into words. Convert the words into lowercase and remove punctionation

In [11]:
#case text to lower case, remove punctuation, remove extra whitepsace in the string and on both sides of the string
data['remove_lower_punct'] = data['content'].str.lower().str.replace("'", '').str.replace('[^\w\s]', ' ').str.replace(" \d+", " ").str.replace(' +', ' ').str.strip()

data.head(5)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: FutureWarning: The default value of regex will change from True to False in a future version.
  


airline_name  ...                                 remove_lower_punct
0            aegean-airlines  ...  lhr to larnaca return plane was clean and in g...
1            aegean-airlines  ...  for a short haul airline the seats are very go...
2                 aer-lingus  ...  the seats are a bit tight but bearable if your...
3                 aer-lingus  ...  appeared new good ptv entertainment seats have...
4  aeroflot-russian-airlines  ...  boeing seats from athens to moscow are so smal...

[5 rows x 22 columns]

In [12]:
data.columns

Index(['airline_name', 'link', 'title', 'author', 'author_country', 'date',
       'content', 'aircraft', 'seat_layout', 'date_flown', 'cabin_flown',
       'type_traveller', 'overall_rating', 'seat_legroom_rating',
       'seat_recline_rating', 'seat_width_rating', 'aisle_space_rating',
       'viewing_tv_rating', 'power_supply_rating', 'seat_storage_rating',
       'recommended', 'remove_lower_punct'],
      dtype='object')

In [13]:
data['tokenise'] = data.apply(lambda row: nltk.word_tokenize(row[21]), axis=1)
data.head(5)

airline_name  ...                                           tokenise
0            aegean-airlines  ...  [lhr, to, larnaca, return, plane, was, clean, ...
1            aegean-airlines  ...  [for, a, short, haul, airline, the, seats, are...
2                 aer-lingus  ...  [the, seats, are, a, bit, tight, but, bearable...
3                 aer-lingus  ...  [appeared, new, good, ptv, entertainment, seat...
4  aeroflot-russian-airlines  ...  [boeing, seats, from, athens, to, moscow, are,...

[5 rows x 23 columns]

In [14]:
import nltk
nltk.download('stopwords')


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [15]:
stop_words = stopwords.words('english')

In [16]:
data['remove_stopwords'] = data['tokenise'].apply(lambda x: [item for item in x if item not in stop_words])

In [17]:
data.head()

airline_name  ...                                   remove_stopwords
0            aegean-airlines  ...  [lhr, larnaca, return, plane, clean, good, con...
1            aegean-airlines  ...  [short, haul, airline, seats, good, find, seat...
2                 aer-lingus  ...  [seats, bit, tight, bearable, youre, courteous...
3                 aer-lingus  ...  [appeared, new, good, ptv, entertainment, seat...
4  aeroflot-russian-airlines  ...  [boeing, seats, athens, moscow, small, table, ...

[5 rows x 24 columns]

In [18]:
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [19]:
wordnet_lemmatizer = WordNetLemmatizer()

# lemmatise words

data['lemmatise'] = data['remove_stopwords'].apply(lambda x: [wordnet_lemmatizer.lemmatize(y) for y in x if y.isalpha()]) 

data.head(5)

airline_name  ...                                          lemmatise
0            aegean-airlines  ...  [lhr, larnaca, return, plane, clean, good, con...
1            aegean-airlines  ...  [short, haul, airline, seat, good, find, seat,...
2                 aer-lingus  ...  [seat, bit, tight, bearable, youre, courteous,...
3                 aer-lingus  ...  [appeared, new, good, ptv, entertainment, seat...
4  aeroflot-russian-airlines  ...  [boeing, seat, athens, moscow, small, table, t...

[5 rows x 25 columns]

In [20]:
from sklearn.feature_extraction.text import TfidfVectorizer
tf_vectorizer = TfidfVectorizer()
corpus=[]
for index, row in data.iterrows():
    corpus.append(", ".join(row[24]))
X = tf_vectorizer.fit_transform(corpus)
tf_vectorizer.get_feature_names_out()
X.shape

(1258, 4932)

In [21]:
vectorizer = CountVectorizer(analyzer = 'word', ngram_range = (2, 2))
                            
# join the processed data to be vectorised

vectors = []

for index, row in data.iterrows():
    vectors.append(", ".join(row[24]))

vectorised = vectorizer.fit_transform(vectors)

print(vectorised)
vectorised.shape

  (0, 17252)	1
  (0, 16406)	1
  (0, 24935)	1
  (0, 22166)	1
  (0, 5340)	1
  (0, 13321)	1
  (0, 6086)	1
  (0, 8149)	1
  (0, 27367)	1
  (0, 30949)	1
  (0, 11173)	1
  (0, 11843)	1
  (0, 13486)	1
  (0, 34336)	1
  (0, 7259)	1
  (0, 14269)	1
  (0, 32697)	1
  (0, 792)	1
  (0, 9358)	1
  (1, 27707)	1
  (1, 13977)	1
  (1, 879)	1
  (1, 26380)	1
  (1, 13351)	1
  (1, 10688)	1
  :	:
  (1257, 24578)	1
  (1257, 33011)	1
  (1257, 12551)	1
  (1257, 30813)	1
  (1257, 9505)	1
  (1257, 31990)	1
  (1257, 23789)	1
  (1257, 16274)	1
  (1257, 22787)	1
  (1257, 7702)	1
  (1257, 8143)	1
  (1257, 20365)	1
  (1257, 8148)	1
  (1257, 24437)	1
  (1257, 7699)	1
  (1257, 2123)	1
  (1257, 19424)	1
  (1257, 4063)	1
  (1257, 19368)	1
  (1257, 7958)	1
  (1257, 1019)	1
  (1257, 1049)	1
  (1257, 16756)	1
  (1257, 9918)	1
  (1257, 22704)	1


(1258, 34721)

In [22]:
# initisalise LDA Model

lda_model = LatentDirichletAllocation(n_components = 10, # number of topics
                                  random_state = 10,          # random state
                                  evaluate_every = -1,      # compute perplexity every n iters, default: Don't
                                  n_jobs = -1,              # Use all available CPUs
                                 )

lda_output = lda_model.fit_transform(vectorised)

# column names

topic_names = ["Topic" + str(i) for i in range(1, lda_model.n_components + 1)]

# make the pandas dataframe

df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns = topic_names)

# get dominant topic for each document

dominant_topic = (np.argmax(df_document_topic.values, axis=1)+1)
df_document_topic['Dominant_topic'] = dominant_topic

# join to original dataframes

data = pd.merge(data, df_document_topic, left_index = True, right_index = True, how = 'outer')
data['Dominant_topic']=data['Dominant_topic'].astype(int)
display(data.head(10))

airline_name  ... Dominant_topic
0            aegean-airlines  ...              2
1            aegean-airlines  ...              5
2                 aer-lingus  ...              1
3                 aer-lingus  ...             10
4  aeroflot-russian-airlines  ...              6
5  aeroflot-russian-airlines  ...              9
6  aeroflot-russian-airlines  ...             10
7  aeroflot-russian-airlines  ...              3
8  aeroflot-russian-airlines  ...              4
9  aeroflot-russian-airlines  ...              1

[10 rows x 36 columns]

In [23]:
''''# initisalise LDA Model on TF IDF

lda_model2 = LatentDirichletAllocation(n_components = 5, # number of topics
                                  random_state = 10,          # random state
                                  evaluate_every = -1,      # compute perplexity every n iters, default: Don't
                                  n_jobs = -1,              # Use all available CPUs
                                 )

lda_output2 = lda_model2.fit_transform(X)

# column names

topic_names2 = ["Topic_Tf_" + str(i) for i in range(1, lda_model.n_components + 1)]

# make the pandas dataframe

df_document_topic2 = pd.DataFrame(np.round(lda_output2, 2), columns = topic_names2)

# get dominant topic for each document

dominant_topic_tf = (np.argmax(df_document_topic2.values, axis=1)+1)
df_document_topic2['Dominant_topic_tf'] = dominant_topic_tf

# join to original dataframes

data = pd.merge(data, df_document_topic2, left_index = True, right_index = True, how = 'outer')
display(data.head(10))
'''

'\'# initisalise LDA Model on TF IDF\n\nlda_model2 = LatentDirichletAllocation(n_components = 5, # number of topics\n                                  random_state = 10,          # random state\n                                  evaluate_every = -1,      # compute perplexity every n iters, default: Don\'t\n                                  n_jobs = -1,              # Use all available CPUs\n                                 )\n\nlda_output2 = lda_model2.fit_transform(X)\n\n# column names\n\ntopic_names2 = ["Topic_Tf_" + str(i) for i in range(1, lda_model.n_components + 1)]\n\n# make the pandas dataframe\n\ndf_document_topic2 = pd.DataFrame(np.round(lda_output2, 2), columns = topic_names2)\n\n# get dominant topic for each document\n\ndominant_topic_tf = (np.argmax(df_document_topic2.values, axis=1)+1)\ndf_document_topic2[\'Dominant_topic_tf\'] = dominant_topic_tf\n\n# join to original dataframes\n\ndata = pd.merge(data, df_document_topic2, left_index = True, right_index = True, how = \'o

In [24]:
# apply sentiment analysis
analyser = SentimentIntensityAnalyzer()

sentiment_score_list = []
sentiment_label_list = []

for i in data['remove_lower_punct'].values.tolist():
    sentiment_score = analyser.polarity_scores(i)

    if sentiment_score['compound'] >= 0.05:
        sentiment_score_list.append(sentiment_score['compound'])
        sentiment_label_list.append('Positive')
    elif sentiment_score['compound'] > -0.05 and sentiment_score['compound'] < 0.05:
        sentiment_score_list.append(sentiment_score['compound'])
        sentiment_label_list.append('Neutral')
    elif sentiment_score['compound'] <= -0.05:
        sentiment_score_list.append(sentiment_score['compound'])
        sentiment_label_list.append('Negative')
    
data['sentiment'] = sentiment_label_list
data['sentiment score'] = sentiment_score_list

data.head()

airline_name  ... sentiment score
0            aegean-airlines  ...          0.9004
1            aegean-airlines  ...          0.7574
2                 aer-lingus  ...          0.9294
3                 aer-lingus  ...          0.1280
4  aeroflot-russian-airlines  ...         -0.0089

[5 rows x 38 columns]

In [25]:
# Topic-Keyword Matrix
df_topic_keywords = pd.DataFrame(lda_model.components_)

# Assign Column and Index
df_topic_keywords.columns = vectorizer.get_feature_names()
df_topic_keywords.index = topic_names

df_topic_no = pd.DataFrame(df_topic_keywords.idxmax())
df_scores = pd.DataFrame(df_topic_keywords.max())

tmp = pd.merge(df_topic_no, df_scores, left_index=True, right_index=True)
tmp.columns = ['topic', 'relevance_score']

display(tmp)

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


topic  relevance_score
aa anyone         Topic10              1.1
aa cabin           Topic7              1.1
aa couldnt         Topic1              1.1
aa customer        Topic1              1.1
aa end             Topic1              1.1
...                   ...              ...
zurich december    Topic7              1.1
zurich hong        Topic8              1.1
zurich leg         Topic4              1.1
zurich lhr         Topic8              1.1
zurich singapore   Topic6              1.1

[34721 rows x 2 columns]

In [26]:
all_topics = []

for i in tmp['topic'].unique():    
    tmp_1 = tmp.loc[tmp['topic'] == i].reset_index()
    tmp_1 = tmp_1.sort_values('relevance_score', ascending=False).head(1)

    tmp_2 = []
    tmp_2.append(tmp_1['topic'].unique()[0])
    tmp_2.append(list(tmp_1['index'].unique()))
    all_topics.append(tmp_2)

all_topics = pd.DataFrame(all_topics, columns=['Dominant_topic', 'topic_name'])
display(all_topics)

Dominant_topic         topic_name
0        Topic10      [window seat]
1         Topic7    [economy class]
2         Topic1       [seat front]
3         Topic6        [long haul]
4         Topic8     [economy seat]
5         Topic2  [premium economy]
6         Topic5         [leg room]
7         Topic9        [tv screen]
8         Topic4        [back seat]
9         Topic3         [exit row]

In [27]:
import altair as alt
alt.Chart(data).mark_bar().encode(
    x='Dominant_topic:N',
    y='count():Q',
    color="sentiment:N"
)

alt.Chart(...)

In [ ]:
!pip install pyldavis